![](https://github.com/bigdata-icict/ETL-Dataiku-DSS/raw/master/tutoriais/pcdas_1.5.png)

# Notebook para criação de tabela de indicadores da PNS -  módulo R 2019 Saúde da Mulher - Parte 2

## Bibliotecas Utilizadas

In [ ]:
#Lendo pacotes necessários
library(survey)
library(ggplot2)
library(dplyr)
library(tictoc)
library(foreign)
library(forcats)
library(tidyverse)

## Carregando microdados da PNS

In [3]:
#Carregando banco de dados para R versão 3.5.0 ou superior
load("<coloque aqui o caminho para o arquivo dos microdados formato RDATA PNS 2013>")

#conferindo as dimensões (número de linhas e colunas)
dim("<Coloque aqui o nome do arquivo RDATA PNS 2019>")

[1] 293726   1087

## Definição do peso e filtragem de respondentes do questionário

In [4]:
#Selecionando registros válidos e calculando peso amostral - summary de verificação
pns2019.1<- pns2019v6 %>% filter(V0015==1)
pns2019.1<-pns2019.1 %>% mutate(peso_morador_selec=((V00291*(94114/168426190))))
pns2019.1<-pns2019.1 %>% filter(!is.na(peso_morador_selec))
summary(pns2019.1$peso_morador_selec)

    Min.  1st Qu.   Median     Mean  3rd Qu.     Max. 
 0.00582  0.27579  0.56358  1.03597  1.16822 63.29775 

## Criação de variáveis dos indicadores

In [5]:
#11. Proporção de mulheres de 18 a 49 anos de idade que tiveram relações sexuais nos últimos 12 meses, ainda menstruam e fazem uso de métodos para evitar a gravidez. - R011P
pns2019.1 <- pns2019.1 %>% mutate(R011P = ifelse(C006 == 2    &
                                                 (C008 >= 18  &
                                                  C008 <= 49) &
                                                 R026 == 1    &
                                                 R031 == 1    &
                                                 R034 == 1, 1, 2))
                                          # ifelse (C006==2 &  C008 >= 18 & C008 <= 49, 2, NA)))
pns2019.1$R011P<-factor(pns2019.1$R011P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2019.1$R011P)


#12. Proporção (%) de mulheres de 18 a 49 anos de idade que já ficaram grávidas - R012P     
pns2019.1 <- pns2019.1 %>% mutate(R012P = ifelse(C006 == 2 & 
                                                 (C008 >= 18 &
                                                  C008 <= 49) &
                                                 S065 == 1, 1, 2))

pns2019.1$R012P<-factor(pns2019.1$R012P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2019.1$R012P)


#13. Proporção de mulheres de 18 a 49 anos de idade que fazem algum tratamento para engravidar.  - R013P
pns2019.1 <- pns2019.1 %>% mutate(R013P = if_else(C006 == 2 & 
                                                 (C008 >= 18 &
                                                  C008 <= 49) &
                                                 (R037 == 1 | 
                                                  R037 == 2), 1, 2, 
                                                     missing=2))
pns2019.1$R013P<-factor(pns2019.1$R013P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2019.1$R013P)

Sim   Não  NA's 
12128 77898   820

Sim   Não 
19374 71472

Sim   Não 
  788 90058

## Definições de abrangências

### Situação urbana ou rural

In [6]:
#Situação Urbano ou Rural
pns2019.1 <- pns2019.1 %>% rename(Sit_Urbano_Rural=V0026)
pns2019.1$Sit_Urbano_Rural<-factor(pns2019.1$Sit_Urbano_Rural, levels=c(1,2), labels=c("urbano", "rural"))
summary(pns2019.1$Sit_Urbano_Rural)

urbano  rural 
 69873  20973

### UF

In [7]:
#Estados - UFs
pns2019.1 <- pns2019.1 %>% rename(Unidades_da_Federacao=V0001)
pns2019.1$Unidades_da_Federacao<-factor(pns2019.1$Unidades_da_Federacao, levels=c(11,12,13,14,15,16,17,21,22,23,24,25,26,27,28,29,31,32,33,35,41,42,43,50,51,52,53),
                                       label=c("Rondônia","Acre","Amazonas","Roraima","Pará","Amapá","Tocantins","Maranhão","Piauí","Ceará",
                                        "Rio Grande do Norte","Paraíba","Pernambuco","Alagoas","Sergipe","Bahia",
                                        "Minas Gerais","Espírito Santo","Rio de Janeiro","São Paulo",
                                        "Paraná","Santa Catarina","Rio Grande do Sul", 
                                        "Mato Grosso do Sul","Mato Grosso","Goiás","Distrito Federal"))
summary(pns2019.1$Unidades_da_Federacao)

Rondônia                Acre            Amazonas             Roraima 
               2176                2380                3479                2238 
               Pará               Amapá           Tocantins            Maranhão 
               3853                1554                1922                5080 
              Piauí               Ceará Rio Grande do Norte             Paraíba 
               2740                4265                2962                3158 
         Pernambuco             Alagoas             Sergipe               Bahia 
               4083                2987                2610                3659 
       Minas Gerais      Espírito Santo      Rio de Janeiro           São Paulo 
               5209                3541                4966                6114 
             Paraná      Santa Catarina   Rio Grande do Sul  Mato Grosso do Sul 
               3967                3738                3767                2863 
        Mato Grosso               Goiás    Distrito Federal 
               2468                2702                2365

### Grandes Regiões

In [8]:
#Grandes Regiões
pns2019.1 <- pns2019.1 %>% 
  mutate(GrandesRegioes = fct_collapse(Unidades_da_Federacao, 
                                          `Norte` = c("Rondônia","Acre","Amazonas","Roraima","Pará", "Amapá","Tocantins"),
                                          `Nordeste` = c("Maranhão", "Piauí", "Ceará", "Rio Grande do Norte", "Paraíba","Pernambuco", "Alagoas","Sergipe","Bahia"),
                                          `Sudeste` = c("Minas Gerais", "Espírito Santo","Rio de Janeiro", "São Paulo"),
                                          `Sul` = c("Paraná", "Santa Catarina", "Rio Grande do Sul"),
                                          `Centro-Oeste`= c("Mato Grosso do Sul","Mato Grosso", "Goiás", "Distrito Federal")))
summary(pns2019.1$GrandesRegioes)

Norte     Nordeste      Sudeste          Sul Centro-Oeste 
       17602        31544        19830        11472        10398

### Capital

In [9]:
#Capital
pns2019.1<- pns2019.1 %>% mutate(Capital= fct_collapse(Unidades_da_Federacao,
                                        `Porto Velho`= "Rondônia", 
                                        `Boa Vista`= "Roraima",              
                                        `Rio Branco`= "Acre", 
                                        `Manaus` = "Amazonas",
                                        `Belém` = "Pará" ,
                                        `Macapá`= "Amapá",
                                        `Palmas` = "Tocantins",
                                        `São Luís` = "Maranhão",
                                        `Teresina`= "Piauí" ,
                                        `Fortaleza`= "Ceará",
                                        `Natal`= "Rio Grande do Norte",
                                        `João Pessoa`= "Paraíba",
                                        `Recife`= "Pernambuco",
                                        `Maceió`= "Alagoas",
                                        `Aracaju`= "Sergipe",
                                        `Salvador`= "Bahia",
                                        `Belo Horizonte`= "Minas Gerais",
                                        `Vitória`= "Espírito Santo",
                                        `Rio de Janeiro`= "Rio de Janeiro",
                                        `São Paulo`= "São Paulo",
                                        `Curitiba`= "Paraná",
                                        `Florianópolis`= "Santa Catarina",
                                        `Porto Alegre`= "Rio Grande do Sul",
                                        `Campo Grande`=  "Mato Grosso do Sul",
                                        `Cuiabá`= "Mato Grosso",
                                        `Goiânia` = "Goiás",
                                        `Brasília`= "Distrito Federal"))
summary(pns2019.1$Capital)

Porto Velho     Rio Branco         Manaus      Boa Vista          Belém 
          2176           2380           3479           2238           3853 
        Macapá         Palmas       São Luís       Teresina      Fortaleza 
          1554           1922           5080           2740           4265 
         Natal    João Pessoa         Recife         Maceió        Aracaju 
          2962           3158           4083           2987           2610 
      Salvador Belo Horizonte        Vitória Rio de Janeiro      São Paulo 
          3659           5209           3541           4966           6114 
      Curitiba  Florianópolis   Porto Alegre   Campo Grande         Cuiabá 
          3967           3738           3767           2863           2468 
       Goiânia       Brasília 
          2702           2365

### Faixa Etária

In [10]:
#Faixas Etárias
pns2019.1 <-  pns2019.1 %>% mutate(faixa_idade=cut(C008,
  breaks = c(17.99, 29.99, 44.99, 59.99),
  labels = c("18 a 29 anos",
             "30 a 44 anos",
             "45 a 59 anos"), 
  ordered_result = TRUE, right = TRUE))
summary(pns2019.1$faixa_idade)

18 a 29 anos 30 a 44 anos 45 a 59 anos         NA's 
       15394        26754        23655        25043

### Raça

In [11]:
#Raça
pns2019.1 <- pns2019.1 %>% mutate(Raca= ifelse(C009==1, 1, 
                        ifelse(C009==2, 2, 
                            ifelse(C009==4, 3, 9))))

pns2019.1$Raca<-factor(pns2019.1$Raca, levels=c(1,2,3),labels=c("Branca", "Preta", "Parda"))

summary(pns2019.1$Raca)

Branca  Preta  Parda   NA's 
 33133  10345  45994   1374

### Renda per capta

In [12]:
#Rendimento domiciliar per capita
pns2019.1 <- pns2019.1 %>% mutate(rend_per_capita = ifelse(VDF004 %in% 1:2, 1, 
                        ifelse(VDF004%in% 3, 2, 
                        ifelse(VDF004%in% 4, 3,
                        ifelse(VDF004%in% 5, 4, 
                        ifelse(is.na(VDF004)==TRUE, NA_real_, 5))))))

pns2019.1$rend_per_capita<-factor(pns2019.1$rend_per_capita, levels=c(1,2,3,4,5), labels=c("Até 1/2 SM","1/2 até 1 SM","1 até 2 SM",
                                                                                   "2 até 3 SM","Mais de 3 SM"))
summary(pns2019.1$rend_per_capita)


Até 1/2 SM 1/2 até 1 SM   1 até 2 SM   2 até 3 SM Mais de 3 SM         NA's 
       23697        26406        22466         7612        10643           22

### Escolaridade

In [13]:
# Escolaridade
pns2019.1 <- pns2019.1 %>% mutate(gescol = ifelse(VDD004A %in% 1:2, 1, 
                        ifelse(VDD004A%in% 3:4, 2, 
                        ifelse(VDD004A%in% 5:6, 3,4
                        ))))

pns2019.1$gescol<-factor(pns2019.1$gescol, levels=c(1,2,3,4), 
                                  labels=c("Fundamental incompleto ou equivalente","Médio incompleto ou equivalente",
                                           "Superior incompleto ou equivalente","Superior completo"))
summary(pns2019.1$gescol)

Fundamental incompleto ou equivalente       Médio incompleto ou equivalente 
                                36276                                 13520 
   Superior incompleto ou equivalente                     Superior completo 
                                27433                                 13617

## Criando indicadores

### Filtrando base de indicadores

In [14]:
#Selecionando variáveis para cálculo de indicadores no survey
pns2019Rsurvey<- pns2019.1 %>% select("V0024","UPA_PNS","peso_morador_selec", "C006", "R011P",
                                       "R012P","R013P","C008","V0031","R026","R031","Sit_Urbano_Rural",
                                       "Unidades_da_Federacao","GrandesRegioes","Capital","faixa_idade",
                                       "Raca","rend_per_capita","gescol")

### Exporta tabela filtrada com os dados específicos - Módulo R 2019

In [15]:
#Salvando csv para cálculo de indicadores no survey
diretorio_saida <- "<coloque aqui o diretório>"
write.csv(pns2019Rsurvey, file.path(diretorio_saida, "pns2019R2survey.csv"))

### Cria plano amostral complexo

In [16]:
desPNSR=svydesign(id=~UPA_PNS,
                  strat=~V0024,
                  weight=~peso_morador_selec,
                  nest=TRUE,
                  data=pns2019Rsurvey)
desPNSR0__P=subset(desPNSR, (C008>=18 & C008<=49) & C006==2)

In [17]:
#survey design R011P
desPNSR011P=subset(desPNSR0__P, !is.na(R011P) & R026 == 1  &  R031 == 1)
desPNSR011P_C=subset(desPNSR011P,  V0031==1)
desPNSR011P_R=subset(desPNSR011P,  !is.na(Raca))
desPNSR011P_FX=subset(desPNSR011P, !is.na(faixa_idade))
desPNSR011P_RE=subset(desPNSR011P, !is.na(rend_per_capita))

In [18]:
#survey design R012P
desPNSR012P=subset(desPNSR0__P, !is.na(R012P))
desPNSR012P_C=subset(desPNSR012P, V0031==1)
desPNSR012P_R=subset(desPNSR012P, !is.na(Raca))
desPNSR012P_FX=subset(desPNSR012P, !is.na(faixa_idade))
desPNSR012P_RE=subset(desPNSR012P, !is.na(rend_per_capita))

In [19]:
#survey design R013P
desPNSR013P=subset(desPNSR0__P, !is.na(R013P))
desPNSR013P_C=subset(desPNSR013P, V0031==1)
desPNSR013P_R=subset(desPNSR013P, !is.na(Raca))
desPNSR013P_FX=subset(desPNSR013P, !is.na(faixa_idade))
desPNSR013P_RE=subset(desPNSR013P, !is.na(rend_per_capita))

### Criação da tabela de indicadores
Essa tabela é responsável por unir os indicadores no formato do painel de indicadores

In [20]:
matrizIndicadores = data.frame()

#### Definição de variáveis para iteração dos indicadores

In [21]:
ListaIndicadores = c(~R011P,~R012P,~R013P)
ListaIndicadoresTexto = c("R011P","R012P","R013P")
ListaTotais = c('Brasil','Capital')
Ano <- "2019"

In [22]:
ListaDominios = c(~Raca,~rend_per_capita,~faixa_idade,~Sit_Urbano_Rural,
                   ~Unidades_da_Federacao,~GrandesRegioes,~Capital,~gescol)
ListaDominiosTexto = c("raça","rend_per_capita","faixa_idade","urb_rur",
                        "uf","região","capital","gescol")

#### Preenchendo a tabela de indicadores
Essas iterações rodam por indicador, abrangência e por design

In [23]:
#Cálculo dos indicadores usando o pacote survey 
i <- 0
matrizIndicadores = data.frame()
#Para cada indicador
for(indicador in ListaIndicadores){
    i <- i + 1
    j <- 1
    print(indicador)
    #Para cada dominio
    for (dominio in ListaDominios){
               #design especifico para capital que é subconjunto do dataframe total
               if (ListaDominiosTexto[j]=="capital"){
                   #designs especificos por variavel que são subconjuntos do dataset total
                   if(ListaIndicadoresTexto[i] == "R011P"){
                     dataframe_indicador<-svyby(indicador, dominio, desPNSR011P_C, svymean,vartype= c("ci", "cv"))
                   }
                   else if(ListaIndicadoresTexto[i] == "R012P"){
                     dataframe_indicador<-svyby(indicador, dominio, desPNSR012P_C, svymean,vartype= c("ci", "cv"))
                   }
                   else {
                     dataframe_indicador<-svyby(indicador, dominio, desPNSR013P_C, svymean,vartype= c("ci", "cv"))
                   }
               #Uso design do subconjunto para raça/cor que inclui preta,branca e parda as outras 
               # conjunto com nulos
               } else if (ListaDominiosTexto[j]=="raça"){
                   if(ListaIndicadoresTexto[i] == "R011P"){
                     dataframe_indicador<-svyby(indicador, dominio, desPNSR011P_R, svymean,vartype= c("ci", "cv"))
                   }
                   else if(ListaIndicadoresTexto[i] == "R012P"){
                     dataframe_indicador<-svyby(indicador, dominio, desPNSR012P_R, svymean,vartype= c("ci", "cv"))
                   }
                   else {
                     dataframe_indicador<-svyby(indicador, dominio, desPNSR013P_R, svymean,vartype= c("ci", "cv"))
                   }

               } else if (ListaDominiosTexto[j]=="rend_per_capita"){
               #design geral para o subconjunto de renda
               # conjunto com nulos
                   if(ListaIndicadoresTexto[i] == "R011P"){
                     dataframe_indicador<-svyby(indicador, dominio, desPNSR011P_RE, svymean,vartype= c("ci", "cv"))
                   }
                   else if(ListaIndicadoresTexto[i] == "R012P"){
                     dataframe_indicador<-svyby(indicador, dominio, desPNSR012P_RE, svymean,vartype= c("ci", "cv"))
                   }
                   else {
                     dataframe_indicador<-svyby(indicador, dominio, desPNSR013P_RE, svymean,vartype= c("ci", "cv"))
                   }
               #design geral para o subconjunto de escolaridade
               # conjunto com nulos
               } else if (ListaDominiosTexto[j]=="faixa_idade"){
                   if(ListaIndicadoresTexto[i] == "R011P"){
                     dataframe_indicador<-svyby(indicador, dominio, desPNSR011P, svymean,vartype= c("ci", "cv"))
                   }
                   else if(ListaIndicadoresTexto[i] == "R012P"){
                     dataframe_indicador<-svyby(indicador, dominio, desPNSR012P, svymean,vartype= c("ci", "cv"))
                   }
                   else {
                     dataframe_indicador<-svyby(indicador, dominio, desPNSR013P_FX, svymean,vartype= c("ci", "cv"))
                   }
               } else if(ListaIndicadoresTexto[i] == "R011P"){
                     dataframe_indicador<-svyby(indicador, dominio, desPNSR011P, svymean,vartype= c("ci", "cv"))
                   } else if(ListaIndicadoresTexto[i] == "R012P"){
                     dataframe_indicador<-svyby(indicador, dominio, desPNSR012P, svymean,vartype= c("ci", "cv"))
                   }
                   else {
                     print(indicador)
                     print(dominio)
                     dataframe_indicador<-svyby(indicador, dominio, desPNSR013P, svymean,vartype= c("ci", "cv"))
                   }
               #União do dataframe de indicadores no formato do painel disponibilizado para PNS
               
               dataframe_indicador<-data.frame(dataframe_indicador)
               
               colnames(dataframe_indicador) <- c("abr_nome","Sim","Nao","LowerS","LowerN","UpperS","UpperN","cvS","cvN")
               dataframe_indicador$Indicador <- ListaIndicadoresTexto[i]
               dataframe_indicador$abr_tipo <- ListaDominiosTexto[j]
               dataframe_indicador$Ano <- Ano
               dataframe_indicador <- dataframe_indicador %>% select("abr_tipo","abr_nome","Ano","Indicador","Sim","LowerS","UpperS","cvS")
               matrizIndicadores <-rbind(matrizIndicadores,dataframe_indicador)
               j <- j + 1
    }
}

~R011P
~R012P
~R013P
~R013P
~Sit_Urbano_Rural
~R013P
~Unidades_da_Federacao
~R013P
~GrandesRegioes
~R013P
~gescol


#### Criando a tabela pela abrangência total

In [24]:
matriz_totais <- data.frame()

#### Preenchendo a tabela com as abrangencia Brasil e total das capitais

In [25]:
i=0
matriz_totais <- data.frame()
#para cada indicador
for(indicador in ListaIndicadores){
    i <- i+1
    #para os totais Brasil e total das capitais
    for(total in ListaTotais){
        dataframe_indicador <- data.frame()
        #Uso do design que é subconjunto do dataset para cada Capital
        if (total == "Capital"){
                   #Indicadores que são subconjunto do dataset tot
                   if(ListaIndicadoresTexto[i] == "R011P"){
                           dataframe_indicador <- svymean(indicador, desPNSR011P_C)
                   }
                   else if(ListaIndicadoresTexto[i] == "R012P"){
                       dataframe_indicador <- svymean(indicador, desPNSR012P_C)
                   }
                   else {
                       dataframe_indicador <- svymean(indicador, desPNSR013P_C)
                   }
        } else {
                   if(ListaIndicadoresTexto[i] == "R011P"){
                           dataframe_indicador <- svymean(indicador, desPNSR011P)
                   }
                   else if(ListaIndicadoresTexto[i] == "R012P"){
                       dataframe_indicador <- svymean(indicador, desPNSR012P)
                   }
                   else {
                       dataframe_indicador <- svymean(indicador, desPNSR013P)
                   }
        }

       intervalo_confianca <- confint(dataframe_indicador)
       coeficiente_variacao <- cv(dataframe_indicador)
       dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(intervalo_confianca))
       dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(coeficiente_variacao))

       dataframe_indicador <- dataframe_indicador %>% 
                               select('mean','X2.5..','X97.5..',coeficiente_variacao) 
        
       dataframe_indicador <- dataframe_indicador %>% 
                                 slice(1)
       colnames(dataframe_indicador) <- c('Sim','LowerS','UpperS','cvS')
       dataframe_indicador <- dataframe_indicador %>% 
                               select('Sim','LowerS','UpperS','cvS')
       dataframe_indicador$Indicador <- ListaIndicadoresTexto[i]
       dataframe_indicador$abr_tipo <- "total"
       dataframe_indicador$abr_nome <- total
       dataframe_indicador$Ano <- Ano 
       dataframe_indicador <- dataframe_indicador %>% 
                            select("abr_tipo","abr_nome","Ano","Indicador",'Sim','LowerS','UpperS','cvS')
       
       matriz_totais <-rbind(matriz_totais,dataframe_indicador)
    }
}

In [26]:
matriz_totais

abr_tipo abr_nome Ano  Indicador Sim        LowerS     UpperS    
R011PSim  total    Brasil   2019 R011P     0.61898824 0.60782933 0.63014715
R011PSim1 total    Capital  2019 R011P     0.63310545 0.61631569 0.64989521
R012PSim  total    Brasil   2019 R012P     0.69668460 0.68527731 0.70809190
R012PSim1 total    Capital  2019 R012P     0.62697606 0.60970696 0.64424516
R013PSim  total    Brasil   2019 R013P     0.02887124 0.02569271 0.03204976
R013PSim1 total    Capital  2019 R013P     0.02649064 0.02201337 0.03096792
          cvS        
R011PSim  0.009197956
R011PSim1 0.013530703
R012PSim  0.008354074
R012PSim1 0.014053054
R013PSim  0.056170977
R013PSim1 0.086232967

#### Unindo tabela de indicadores e de totais

In [27]:
matrizIndicadores<-rbind(matrizIndicadores,matriz_totais)

In [28]:
unique(matrizIndicadores$abr_tipo)

[1] "raça"            "rend_per_capita" "faixa_idade"     "urb_rur"        
[5] "uf"              "região"          "capital"         "gescol"         
[9] "total"

In [43]:
matrizIndicadores[matrizIndicadores$abr_tipo=='raça' & 
                  matrizIndicadores$Indicador=='R013P', ]

abr_tipo abr_nome Ano  Indicador Sim        LowerS     UpperS    
Branca2 raça     Branca   2019 R013P     0.03306502 0.02744131 0.03868872
Preta2  raça     Preta    2019 R013P     0.02032630 0.01280439 0.02784820
Parda2  raça     Parda    2019 R013P     0.02777239 0.02354443 0.03200036
        cvS       
Branca2 0.08677727
Preta2  0.18880847
Parda2  0.07767293

#### Visualizando tabela de indicadores

In [39]:
matrizIndicadores

abr_tipo       
Branca                                 raça           
Preta                                  raça           
Parda                                  raça           
Até 1/2 SM                             rend_per_capita
1/2 até 1 SM                           rend_per_capita
1 até 2 SM                             rend_per_capita
2 até 3 SM                             rend_per_capita
Mais de 3 SM                           rend_per_capita
18 a 29 anos                           faixa_idade    
30 a 44 anos                           faixa_idade    
45 a 59 anos                           faixa_idade    
urbano                                 urb_rur        
rural                                  urb_rur        
Rondônia                               uf             
Acre                                   uf             
Amazonas                               uf             
Roraima                                uf             
Pará                                   uf             
Amapá                                  uf             
Tocantins                              uf             
Maranhão                               uf             
Piauí                                  uf             
Ceará                                  uf             
Rio Grande do Norte                    uf             
Paraíba                                uf             
Pernambuco                             uf             
Alagoas                                uf             
Sergipe                                uf             
Bahia                                  uf             
Minas Gerais                           uf             
⋮                                      ⋮              
São Luís2                              capital        
Teresina2                              capital        
Fortaleza2                             capital        
Natal2                                 capital        
João Pessoa2                           capital        
Recife2                                capital        
Maceió2                                capital        
Aracaju2                               capital        
Salvador2                              capital        
Belo Horizonte2                        capital        
Vitória2                               capital        
Rio de Janeiro5                        capital        
São Paulo4                             capital        
Curitiba2                              capital        
Florianópolis2                         capital        
Porto Alegre2                          capital        
Campo Grande2                          capital        
Cuiabá2                                capital        
Goiânia2                               capital        
Brasília2                              capital        
Fundamental incompleto ou equivalente2 gescol         
Médio incompleto ou equivalente2       gescol         
Superior incompleto ou equivalente2    gescol         
Superior completo2                     gescol         
R011PSim                               total          
R011PSim1                              total          
R012PSim                               total          
R012PSim1                              total          
R013PSim                               total          
R013PSim1                              total          
                                       abr_nome                             
Branca                                 Branca                               
Preta                                  Preta                                
Parda                                  Parda                                
Até 1/2 SM                             Até 1/2 SM                           
1/2 até 1 SM                           1/2 até 1 SM                         
1 até 2 SM                             1 até 2 SM                           
2 até 3 SM                             2 até 3 SM                           
Mais de 3 SM 

#### Exportando tabela de indicadores calculados - Módulo R 2019

In [40]:
diretorio_saida <- "<coloque aqui o diretório>"
write.table(matrizIndicadores,file=paste0(diretorio_saida, "Indicadores_2019R2_R.csv"),sep = ";",dec = ",",row.names = FALSE)